# Trapezoidal integration formula and Richardson extrapolation

<div style="height:15cm;">
Trapezoidal rule with the integration step $h$:
$$
\int_a^b f(x) \, \mathrm{d}x =
\frac{h}{2} \left[
f(x_1) + 2f(x_2) + 2f(x_3) + 2f(x_4)+ \ldots + 2f(x_{n-1}) + f(x_n)
\right] + \alpha h^2  + O(h^p) = T(h, n) + \alpha h^2  + O(h^p) , \tag{1}
$$
where for later use we defined
$$T(h, n) \equiv \frac{h}{2} \left[
f(x_1) + 2f(x_2) + 2f(x_3) + 2f(x_4)+ \ldots + 2f(x_{n-1}) + f(x_n)
\right] , \tag{2}$$
and
$$
h = \frac{b-a}{n - 1},
$$
$$
x_i = a + (i - 1) \, h, \quad i = 1, \ldots, n,
$$
$\alpha h^2$ is the leading discretization error term of the
algorithm, the coefficient $\alpha$ is unknown. The term $O(h^p)$
indicates the higher order error terms, $p > 2$. 
</div>

In [ ]:
using PyPlot

In [ ]:
"""
    ans = mytrapezoids(fun, a, b, n)

Numerically evaluate the integral int_a^b fun(x) dx using the
trapezoidal rule: I = h/2*(f_1 + 2f_2 + ... + 2f_{n-1} + f_n),
where h = (b - a)/(n - 1), x_i = a + (i - 1)*h, f_i = fun(x_i).
"""
function mytrapezoids(fun, a, b, n)
    h = (b - a)/(n - 1)
    s1 = fun(a) + fun(b)
    s2 = 0.0
    for i = 2:(n-1)
        s2 += fun(a + (i-1)*h)
    end
    return (s1 + 2*s2)*h/2
end

### Testing

In [ ]:
# Simple test 1
fun1(x) = x
a = -1.0
b = 1.0
np = 20
exact = 0.0
abs(mytrapezoids(fun1, a, b, np) - exact)  

In [ ]:
# Simple test 2
fun2(x) = exp(x)
a = 0.0
b = 1.0
np = 200
exact = exp(1) - 1.0
abs(mytrapezoids(fun2, a, b, np) - exact)

### Error of trapezoidal formula

In [ ]:
# An analysis of the error of trapezoidal rule vs integration step h
fun0(x) = sin(x)
a = 0.0
b = pi
exact = 2.0
ndp = 10
errt = zeros(ndp)
hh = zeros(ndp);

In [ ]:
for k = 1:ndp 
    np = 2^k + 1
    hh[k] = (b - a)/(np - 1)
    errt[k] = abs(mytrapezoids(fun0, a, b, np) - exact)
end

In [ ]:
loglog(hh, errt, label="numerical experiment", marker=".")
loglog(hh, hh .^ 2, linestyle="dashed", label=L"hh^2")
grid(true)
xlabel("integration step")
ylabel("absolute error")
title("Error of trapezoidal rule")
legend();

## Richardson extrapolation

Recall that 
$$\int_a^b f(x) \, \mathrm{d}x = T(h, n) + \alpha h^2  + O(h^p),$$ where $T(h, n)$ is given by Eq. (2).

Next, we write down the trapezoidal rule with step $2h$. It will involve
only the nodes at $x_1$, $x_3$, $x_5$, $\ldots$, $x_{n-2}$, $x_n$:

$$\int_a^b f(x) \, \mathrm{d}x = h [ f(x_1) + 2f(x_3) + 2f(x_5) + \ldots + 2f(x_{n-2}) + f(x_n) ] + \alpha (2h)^2  + O(h^p) 
= T(2h) + 4\alpha h^2  + O(h^p) . \tag{3}$$

The leading error in Eq. (3) is 4 times the error in Eq. (2), since we doubled the step size. So we multiply both sides of Eq. (2) by 4,

$$
4\int_a^b f(x) \, \mathrm{d}x = 4T(h) + 4\alpha h^2 + O(h^p),  \tag{4}
$$
and subtract Eq. (3) from Eq. (4), intending to
cancel out the leading error term. The result that we get is the
*Simpson's formula*:

$$
\int_a^b f(x) \, \mathrm{d}x  = \frac{1}{3}\left(4T(h) - T(2h) \right) + O(h^p) .
$$

### Simpson's formula

In [ ]:
"""
    ans = mytrapezoids2(f, h)

Numerically evaluate the integral int_a^b fun(x) dx using the
trapezoidal rule: I = h/2*(f[1] + 2f[2] + ... + 2f[n-1] + f[n]),
where h = (b - a)/(n - 1), x_i = a + (i - 1)*h, f[i] = fun(x_i).
"""
function mytrapezoids2(fvec, h)
    s1 = fvec[1] + fvec[end]
    s2 = sum(fvec)
    return (2*s2 - s1)*h/2
end

In [ ]:
"""
    ans = mysimpsons2(fvec, h)

Numerically evaluate the integral int_a^b fun(x) dx using the
Simpson's rule, where h = (b - a)/(n - 1), x_i = a + (i - 1)*h, fvec[i] = fun(x_i).
"""
function mysimpsons2(fvec, h)
    n = length(fvec)
    t1 = mytrapezoids2(fvec, h)
    t2 = mytrapezoids2(fvec[1:2:n], 2*h)
    return (4*t1 - t2)/3
end

In [ ]:
# Simple test 1
fun1(x) = x
a = -1.0
b = 1.0
np = 21
exact = 0.0
xx = range(a, b, np)
h = xx[2] - xx[1]
fvec = fun1.(xx)
abs(mysimpsons2(fvec, h) - exact)  

In [ ]:
# Simple test 2
fun2(x) = exp(x)
a = 0.0
b = 1.0
np = 201
exact = exp(1.0) - 1.0
xx = range(a, b, np)
h = xx[2] - xx[1]
fvec = fun2.(xx)
abs(mysimpsons2(fvec, h) - exact) 

### Error of the Simpson's formula

An analysis of the error of Simpson's rule vs integration step h

In [ ]:
fun0(x) = sin(x)
a = 0.0
b = pi
exact = 2.0
ndp = 10
errs = zeros(ndp)
hh = zeros(ndp);

In [ ]:
for k = 1:ndp 
    np = 2^k + 1
    xx = range(a, b, np)
    h = xx[2] - xx[1]
    hh[k] = h
    fun0vec = fun0.(xx)
    errs[k] = abs(mysimpsons2(fun0vec, h) - exact)
end

In [ ]:
loglog(hh, errs, label="numerical experiment", marker=".")
loglog(hh, hh .^ 4, linestyle="dashed", label=L"hh^4")
grid(true)
xlabel("integration step")
ylabel("absolute error")
title("Error of Simpson's rule")
legend();

In [ ]:
loglog(hh, errs, label="Simpson's", marker=".")
loglog(hh, errt, label="Trapezoidal", marker=".")
loglog(hh, hh .^ 4 / 1000, linestyle="dashed", label=L"hh^4")
loglog(hh, hh .^ 2, linestyle="dotted", label=L"hh^2")
grid(true)
xlabel("integration step")
ylabel("absolute error")
title("Errors of Simpson's and trapezoidal rules")
legend();